In [1]:
import os
import pickle
import random

# from bds.fpgrowth import preprocess_transaction_list, build_fptree, fpgrowth_on_tree
# from bds.bb import get_ground_truth_count
# from bds.bbSampleTreeApproxCounting import BranchAndBoundNaive
import time
from time import time

import gmpy2 as gmp
import numpy as np
import pandas as pd
from gmpy2 import mpfr, mpz
from ortools.linear_solver import pywraplp
from ortools.sat.python import cp_model
from scipy.sparse import random

from bds.fpgrowth import build_fptree, fpgrowth_on_tree, preprocess_transaction_list
from bds.rule import Rule

In [2]:
def generate_random_sparse_binary_matrix(rows, cols, density):
    # Generate a random binary matrix with the specified density (percentage of non-zero elements)
    random_matrix = random(rows, cols, density=density, format="csr", dtype=np.float64)
    random_matrix.data = np.array(
        random_matrix.data >= 0.5, dtype=np.int64
    )  # Threshold to get binary values
    return random_matrix


class VarArraySolutionPrinter(cp_model.CpSolverSolutionCallback):
    """Print intermediate solutions."""

    def __init__(self, variables):
        cp_model.CpSolverSolutionCallback.__init__(self)
        self.__variables = variables
        self.__solution_count = 0

    def on_solution_callback(self):
        self.__solution_count += 1
        for v in self.__variables:
            print("%s=%i" % (v, self.Value(v)), end=" ")
        print()

    def solution_count(self):
        return self.__solution_count


def solve_sat_with_min_max(n, n_positives, n_negatives, N, P, lambd, epsilon):
    model = cp_model.CpModel()

    m = len(P[0])

    # Constraints for min function
    x = [model.NewBoolVar(f"x{i}") for i in range(m)]
    zFP = [
        model.NewBoolVar(f"FP{i}") for i in range(n_negatives)
    ]  # Auxiliary variables z_i with lower bound 0 and upper bound 1
    zFN = [model.NewBoolVar(f"FN{i}") for i in range(n_positives)]

    zFPpre = [
        model.NewBoolVar(f"preFP{i}") for i in range(n_negatives)
    ]  # Auxiliary variables z_i with lower bound 0 and upper bound 1
    zFNpre = [model.NewBoolVar(f"preFN{i}") for i in range(n_positives)]

    sum_var_positive = model.NewIntVar(0, n_positives, "sumPos")
    sum_var_negative = model.NewIntVar(0, n_negatives, "sumNeg")
    sum_var_x = model.NewIntVar(0, m, "sumx")
    target = model.NewIntVar(0, n, "target")

    #
    for i in range(n_negatives):
        model.Add(zFPpre[i] == sum([N[i][j] * x[j] for j in range(m)]))
        model.AddMinEquality(zFP[i], [zFPpre[i], 1])
    #
    # for i in range(n_negatives):
    #    model.AddMinEquality(zFP[i], [ sum([N[i][j] * x[j] for j in range(m)]) , 1]) # should be either 0 if the innter product is 0 or 1
    #
    #
    #
    for i in range(n_positives):
        model.Add(zFNpre[i] == sum([P[i][j] * x[j] for j in range(m)]))
        model.AddMaxEquality(zFN[i], [1 - zFNpre[i], 0])  # also 0 or 1

    model.Add(sum_var_positive == sum(zFN))

    model.Add(sum_var_negative == sum(zFP))

    model.Add(sum_var_x == sum(x))

    model.Add(
        sum_var_positive + sum_var_negative + lambd * n * sum_var_x <= epsilon * n
    )

    # Create a solver
    # solver = cp_model.CpSolver()
    #
    # Find all feasible solutions
    # count = 0
    # while solver.NextSolution():
    #    count += 1
    #    print(f"Feasible Solution {count}:")
    #    for i in range(1, 6):
    #        print(f"x{i} = {solver.Value(x[i-1])}")

    solver = cp_model.CpSolver()
    # solution_printer = VarArraySolutionPrinter([x])
    ## Enumerate all solutions.
    # solver.parameters.enumerate_all_solutions = True
    # Solve.
    status = solver.Solve(model)
    # solver.SearchForAllSolutions(model, solution_printer)
    # count = 0

    if status == cp_model.OPTIMAL or status == cp_model.FEASIBLE:
        print("printing solutions... ")
        solution_printer = VarArraySolutionPrinter([x[i] for i in range(len(x))])
        ## Enumerate all solutions.
        solver.parameters.enumerate_all_solutions = True
        # Solve..
        status = solver.Solve(model, solution_printer)
        # print('x = %i' % solver.Value(x[0]))
    else:
        print("No solution found.")

    return model

In [3]:
N = [[1, 0], [0, 1]]
P = [[1, 0], [0, 1]]

n = 4
cols = 2
rows_positive = 2
rows_negative = 2

In [66]:
model = solve_sat_with_min_max(
    n, rows_positive, rows_negative, N, P, lambd=1, epsilon=1
)

printing solutions... 
x0=0 x1=0 
x0=0 x1=0 
x0=0 x1=0 
x0=0 x1=0 
x0=0 x1=0 


In [5]:
model = solve_sat_with_min_max(
    n, rows_positive, rows_negative, N, P, lambd=1, epsilon=4
)

printing solutions... 
x0=0 x1=0 
x0=0 x1=1 
x0=1 x1=0 
x0=1 x1=1 


In [6]:
model = solve_sat_with_min_max(
    n, rows_positive, rows_negative, N, P, lambd=1, epsilon=2
)

printing solutions... 
x0=0 x1=0 


In [ ]:
# the above is correct!

In [ ]:
# Generate two random binary sparse matrices
rows_positive = 5  # Number of rows in the matrix
rows_negative = 6
n = rows_negative + rows_positive
cols = 4  # Number of columns in the matrix
density = 0.8  # Density of non-zero elements (percentage)

matrix1 = generate_random_sparse_binary_matrix(rows_negative, cols, density)
matrix2 = generate_random_sparse_binary_matrix(rows_positive, cols, density)

# N = generate_random_sparse_binary_matrix(rows, cols, density)
# P = generate_random_sparse_binary_matrix(rows, cols, density)

# Convert the sparse matrices to nested lists for OR-Tools
N = matrix1.toarray().tolist()
P = matrix2.toarray().tolist()

In [ ]:
model = solve_sat_with_min_max(
    n, rows_positive, rows_negative, N, P, lambd=0, epsilon=100000000000000000
)

In [ ]:
N

In [ ]:
# solver = cp_model.CpSolver()
# solution_printer = VarArraySolutionPrinter([x, y, z])
## Enumerate all solutions.
##solver.parameters.enumerate_all_solutions = True
# Solve.
# status = solver.Solve(model, solution_printer)

In [ ]:
# Generate two random binary sparse matrices
rows = 5  # Number of rows in the matrix
cols = 6  # Number of columns in the matrix
density = 0.3  # Density of non-zero elements (percentage)

matrix1 = generate_random_sparse_binary_matrix(rows, cols, density)
matrix2 = generate_random_sparse_binary_matrix(rows, cols, density)

N = generate_random_sparse_binary_matrix(rows, cols, density)
P = generate_random_sparse_binary_matrix(rows, cols, density)

# Convert the sparse matrices to nested lists for OR-Tools
N = matrix1.toarray().tolist()
P = matrix2.toarray().tolist()

In [3]:
# solutions = solve_integer_program(rows, cols, N, P, 0.0, 1)

In [4]:
os.getcwd()

'/u/50/ciaperm1/unix/sampling-rashomon-decision-set-code/notebooks'

In [5]:
# Load the CSV file using Pandas
data = pd.read_csv("../data/compas_test-binary.csv")

# Print the data
data.head()
#
X = data.to_numpy()
#

In [6]:
# read labels
f = open("../data/compas_test.label")
labels = []
for row in f.readlines():
    labels.append(list(map(int, row.split(" ")[1:])))

In [7]:
%cd ..

/u/50/ciaperm1/unix/sampling-rashomon-decision-set-code


In [8]:
def mpz_set_bits(n: mpz, bits: np.ndarray) -> mpz:
    """return a copy of n and set `bits` to 1 in `n`"""
    for i in bits:
        n = gmp.bit_set(n, int(i))
    return n


def compute_truthtable(X, itemset):
    """poorly optimized function"""
    support_list = []
    for i in range(X.shape[0]):
        if sum([X[i][j] for j in itemset]) == len(itemset):
            support_list.append(i)

    truthtable = mpz_set_bits(mpz(), support_list)

    return truthtable, support_list

In [9]:
y = np.array(labels[1], dtype=bool)
X_bag = [{j for j, x in enumerate(row) if x} for row in X]


for min_support in [7, 10, 20, 30, 40, 50][::-1]:
    ordered_input_data = preprocess_transaction_list(X_bag, min_support)
    tree = build_fptree(ordered_input_data)
    frequent_itemsets = set(fpgrowth_on_tree(tree, set(), min_support))

    print(len(frequent_itemsets))

61
77
104
151
262
312


In [10]:
[7, 10, 20, 30, 40, 50][::-1]

[50, 40, 30, 20, 10, 7]

In [ ]:
y = np.array(labels[1], dtype=bool)
X_bag = [{j for j, x in enumerate(row) if x} for row in X]


for min_support in [7, 10, 20, 30, 40, 50][::-1]:
    ordered_input_data = preprocess_transaction_list(X_bag, min_support)
    tree = build_fptree(ordered_input_data)
    frequent_itemsets = set(fpgrowth_on_tree(tree, set(), min_support))

    print(len(frequent_itemsets))

    PD = X[y]
    ND = X[~y]

    N = np.zeros((ND.shape[0], len(frequent_itemsets)))
    P = np.zeros((PD.shape[0], len(frequent_itemsets)))

    # create map
    positive_counter = 0
    negative_counter = 0
    map_positive = dict()
    map_negative = dict()

    for i in range(X.shape[0]):
        if y[i]:
            map_positive[i] = positive_counter
            positive_counter += 1
        else:
            map_negative[i] = negative_counter
            negative_counter += 1

    # Now create rules
    rules = []
    for i, itemset in enumerate(frequent_itemsets):
        tt, support_list = compute_truthtable(X, itemset)
        this_Rule = Rule(
            id=i + 1, name="rule_" + str(i), cardinality=len(itemset), truthtable=tt
        )
        # we need the truthtable for this itemset
        rules.append(this_Rule)

        for example in support_list:
            if y[example]:
                P[map_positive[example], i] = 1
            else:
                N[map_negative[example], i] = 1

    # dimension of x
    print("number of rules: " + str(len(rules)))

    # record time
    t = time.time()
    n = X.shape[0]
    rows_positive = P.shape[0]
    rows_negative = N.shape[0]
    solutions = solve_sat_with_min_max(
        n, rows_positive, rows_negative, N, P, lambd=1, epsilon=1000
    )  # solve_integer_program(n, m, N, P, lmbd, ub)
    elapsed = time.time() - t
    all_times.append(elapsed)

In [ ]:
min_support = 160
ordered_input_data = preprocess_transaction_list(X_bag, min_support)

tree = build_fptree(ordered_input_data)
frequent_itemsets = set(fpgrowth_on_tree(tree, set(), min_support))

PD = X[y]
ND = X[~y]

N = np.zeros((ND.shape[0], len(frequent_itemsets)))
P = np.zeros((PD.shape[0], len(frequent_itemsets)))

# create map
positive_counter = 0
negative_counter = 0
map_positive = dict()
map_negative = dict()

for i in range(X.shape[0]):
    if y[i]:
        map_positive[i] = positive_counter
        positive_counter += 1
    else:
        map_negative[i] = negative_counter
        negative_counter += 1


# Now create rules
rules = []
for i, itemset in enumerate(frequent_itemsets):
    tt, support_list = compute_truthtable(X, itemset)
    this_Rule = Rule(
        id=i + 1, name="rule_" + str(i), cardinality=len(itemset), truthtable=tt
    )
    # we need the truthtable for this itemset
    rules.append(this_Rule)

    for example in support_list:
        if y[example]:
            P[map_positive[example], i] = 1
        else:
            N[map_negative[example], i] = 1

In [11]:
all_times = []

for this_support in [160, 140, 120, 100, 80, 60, 40]:
    ordered_input_data = preprocess_transaction_list(X_bag, min_support)

    tree = build_fptree(ordered_input_data)
    frequent_itemsets = set(fpgrowth_on_tree(tree, set(), this_support))

    PD = X[y]
    ND = X[~y]

    N = np.zeros((ND.shape[0], len(frequent_itemsets)))
    P = np.zeros((PD.shape[0], len(frequent_itemsets)))

    # create map
    positive_counter = 0
    negative_counter = 0
    map_positive = dict()
    map_negative = dict()

    for i in range(X.shape[0]):
        if y[i]:
            map_positive[i] = positive_counter
            positive_counter += 1
        else:
            map_negative[i] = negative_counter
            negative_counter += 1

    # Now create rules
    rules = []
    for i, itemset in enumerate(frequent_itemsets):
        tt, support_list = compute_truthtable(X, itemset)
        this_Rule = Rule(
            id=i + 1, name="rule_" + str(i), cardinality=len(itemset), truthtable=tt
        )
        # we need the truthtable for this itemset
        rules.append(this_Rule)

        for example in support_list:
            if y[example]:
                P[map_positive[example], i] = 1
            else:
                N[map_negative[example], i] = 1

    # dimension of x
    print("number of rules: " + str(len(rules)))

    # record time
    t = time.time()
    n = X.shape[0]
    rows_positive = P.shape[0]
    rows_negative = N.shape[0]
    solutions = solve_sat_with_min_max(
        n, rows_positive, rows_negative, N, P, lambd=1, epsilon=1000
    )  # solve_integer_program(n, m, N, P, lmbd, ub)
    elapsed = time.time() - t
    all_times.append(elapsed)

TypeError: '<' not supported between instances of 'str' and 'int'

In [11]:
all_times = []


def custom_print(*args, **kwargs):
    # You can log the output to a file or ignore it altogether
    pass


# Redefine the print function inside your function
# original_print = print
# print = custom_print
# print = original_print


for this_support in [7, 10, 20, 30, 40, 50][::-1]:
    ordered_input_data = preprocess_transaction_list(X_bag, this_support)

    tree = build_fptree(ordered_input_data)
    frequent_itemsets = set(fpgrowth_on_tree(tree, set(), this_support))

    PD = X[y]
    ND = X[~y]

    N = np.zeros((ND.shape[0], len(frequent_itemsets)))
    P = np.zeros((PD.shape[0], len(frequent_itemsets)))

    # create map
    positive_counter = 0
    negative_counter = 0
    map_positive = dict()
    map_negative = dict()

    for i in range(X.shape[0]):
        if y[i]:
            map_positive[i] = positive_counter
            positive_counter += 1
        else:
            map_negative[i] = negative_counter
            negative_counter += 1

    # Now create rules
    rules = []
    for i, itemset in enumerate(frequent_itemsets):
        tt, support_list = compute_truthtable(X, itemset)
        this_Rule = Rule(
            id=i + 1, name="rule_" + str(i), cardinality=len(itemset), truthtable=tt
        )
        # we need the truthtable for this itemset
        rules.append(this_Rule)

        for example in support_list:
            if y[example]:
                P[map_positive[example], i] = 1
            else:
                N[map_negative[example], i] = 1

    # dimension of x
    print("number of rules: " + str(len(rules)))

    # record time
    t = time.time()
    n = X.shape[0]
    rows_positive = P.shape[0]
    rows_negative = N.shape[0]
    solutions = solve_sat_with_min_max(
        n, rows_positive, rows_negative, N, P, lambd=1, epsilon=1
    )  # solve_integer_program(n, m, N, P, lmbd, ub)
    elapsed = time.time() - t
    all_times.append(elapsed)

number of rules: 61
printing solutions... 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x4

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x4

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x4

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 
x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x4

...

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 x61=0 x62=0 x63=0 x64=0 x65=0 x66=0 x67=0 x68=0 x69=0 x70=0 x71=0 x72=0 x73=0 x74=0 x75=0 x76=0 x77=0 x78=0 x79=0 x80=0 x81=0 x82=0 x83=0 x84=0 x85=0 x86=0 x87=0 x88=0 x89=0 x90=0 x91=0 x92=0 x93=0 x94=0 x95=0 x96=0 x97=0 x98=0 x99=0 x100=0 x101=0 x102=0 x103=0 x104=0 x105=0 x106=0 x107=0 x108=0 x109=0 x110=0 x111=0 x112=0 x113=0 x114=0 x115=0 x116=0 x117=0 x118=0 x119=0 x120=0 x121=0 x122=0 x123=0 x124=0 x125=0 x126=0 x127=0 x128=0 x129=0 x130=0 x131=0 x132=0 x133=0 x134=0 x135=0 x136=0 x137=0 x138=0 x139=0 x140=0 x141=0 x142=0 x143=0 x144=0 x145=0 x146=0 x147=0 x148=0 x149=0 x150=0 x151=0 x152=0 x153=0 x154=0 x155=0 x156=0 x157=0 x158

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 x61=0 x62=0 x63=0 x64=0 x65=0 x66=0 x67=0 x68=0 x69=0 x70=0 x71=0 x72=0 x73=0 x74=0 x75=0 x76=0 x77=0 x78=0 x79=0 x80=0 x81=0 x82=0 x83=0 x84=0 x85=0 x86=0 x87=0 x88=0 x89=0 x90=0 x91=0 x92=0 x93=0 x94=0 x95=0 x96=0 x97=0 x98=0 x99=0 x100=0 x101=0 x102=0 x103=0 x104=0 x105=0 x106=0 x107=0 x108=0 x109=0 x110=0 x111=0 x112=0 x113=0 x114=0 x115=0 x116=0 x117=0 x118=0 x119=0 x120=0 x121=0 x122=0 x123=0 x124=0 x125=0 x126=0 x127=0 x128=0 x129=0 x130=0 x131=0 x132=0 x133=0 x134=0 x135=0 x136=0 x137=0 x138=0 x139=0 x140=0 x141=0 x142=0 x143=0 x144=0 x145=0 x146=0 x147=0 x148=0 x149=0 x150=0 x151=0 x152=0 x153=0 x154=0 x155=0 x156=0 x157=0 x158

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 x61=0 x62=0 x63=0 x64=0 x65=0 x66=0 x67=0 x68=0 x69=0 x70=0 x71=0 x72=0 x73=0 x74=0 x75=0 x76=0 x77=0 x78=0 x79=0 x80=0 x81=0 x82=0 x83=0 x84=0 x85=0 x86=0 x87=0 x88=0 x89=0 x90=0 x91=0 x92=0 x93=0 x94=0 x95=0 x96=0 x97=0 x98=0 x99=0 x100=0 x101=0 x102=0 x103=0 x104=0 x105=0 x106=0 x107=0 x108=0 x109=0 x110=0 x111=0 x112=0 x113=0 x114=0 x115=0 x116=0 x117=0 x118=0 x119=0 x120=0 x121=0 x122=0 x123=0 x124=0 x125=0 x126=0 x127=0 x128=0 x129=0 x130=0 x131=0 x132=0 x133=0 x134=0 x135=0 x136=0 x137=0 x138=0 x139=0 x140=0 x141=0 x142=0 x143=0 x144=0 x145=0 x146=0 x147=0 x148=0 x149=0 x150=0 x151=0 x152=0 x153=0 x154=0 x155=0 x156=0 x157=0 x158

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 x61=0 x62=0 x63=0 x64=0 x65=0 x66=0 x67=0 x68=0 x69=0 x70=0 x71=0 x72=0 x73=0 x74=0 x75=0 x76=0 x77=0 x78=0 x79=0 x80=0 x81=0 x82=0 x83=0 x84=0 x85=0 x86=0 x87=0 x88=0 x89=0 x90=0 x91=0 x92=0 x93=0 x94=0 x95=0 x96=0 x97=0 x98=0 x99=0 x100=0 x101=0 x102=0 x103=0 x104=0 x105=0 x106=0 x107=0 x108=0 x109=0 x110=0 x111=0 x112=0 x113=0 x114=0 x115=0 x116=0 x117=0 x118=0 x119=0 x120=0 x121=0 x122=0 x123=0 x124=0 x125=0 x126=0 x127=0 x128=0 x129=0 x130=0 x131=0 x132=0 x133=0 x134=0 x135=0 x136=0 x137=0 x138=0 x139=0 x140=0 x141=0 x142=0 x143=0 x144=0 x145=0 x146=0 x147=0 x148=0 x149=0 x150=0 x151=0 x152=0 x153=0 x154=0 x155=0 x156=0 x157=0 x158

x0=0 x1=0 x2=0 x3=0 x4=0 x5=0 x6=0 x7=0 x8=0 x9=0 x10=0 x11=0 x12=0 x13=0 x14=0 x15=0 x16=0 x17=0 x18=0 x19=0 x20=0 x21=0 x22=0 x23=0 x24=0 x25=0 x26=0 x27=0 x28=0 x29=0 x30=0 x31=0 x32=0 x33=0 x34=0 x35=0 x36=0 x37=0 x38=0 x39=0 x40=0 x41=0 x42=0 x43=0 x44=0 x45=0 x46=0 x47=0 x48=0 x49=0 x50=0 x51=0 x52=0 x53=0 x54=0 x55=0 x56=0 x57=0 x58=0 x59=0 x60=0 x61=0 x62=0 x63=0 x64=0 x65=0 x66=0 x67=0 x68=0 x69=0 x70=0 x71=0 x72=0 x73=0 x74=0 x75=0 x76=0 x77=0 x78=0 x79=0 x80=0 x81=0 x82=0 x83=0 x84=0 x85=0 x86=0 x87=0 x88=0 x89=0 x90=0 x91=0 x92=0 x93=0 x94=0 x95=0 x96=0 x97=0 x98=0 x99=0 x100=0 x101=0 x102=0 x103=0 x104=0 x105=0 x106=0 x107=0 x108=0 x109=0 x110=0 x111=0 x112=0 x113=0 x114=0 x115=0 x116=0 x117=0 x118=0 x119=0 x120=0 x121=0 x122=0 x123=0 x124=0 x125=0 x126=0 x127=0 x128=0 x129=0 x130=0 x131=0 x132=0 x133=0 x134=0 x135=0 x136=0 x137=0 x138=0 x139=0 x140=0 x141=0 x142=0 x143=0 x144=0 x145=0 x146=0 x147=0 x148=0 x149=0 x150=0 x151=0 x152=0 x153=0 x154=0 x155=0 x156=0 x157=0 x158

In [ ]:
all_times[:-1]

In [ ]:
[7, 10, 20, 30, 40, 50][::-1][:4]

In [ ]:
m = len(rules)
# lmbd = 0.0
# ub = 4000000000000000000000000000000000
# solutions = solve_integer_program(n, m, N, P, lmbd, ub)
m

In [ ]:
solutions